In [0]:
import pandas as pd
import scipy.stats
from datetime import datetime
import matplotlib.pyplot as plt
import numpy as np
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql import SparkSession, functions as F
import pyspark.sql.functions as f
import os 
import math
# Disable warnings, set Matplotlib inline plotting and load Pandas package
import warnings
warnings.filterwarnings('ignore')

## Data Exploration

In [0]:
item_features = spark.read.csv('/FileStore/tables/item_features.csv', header=True).withColumn(
    'feature_category_id',
    concat(
        lit('cat_'),
        col('feature_category_id')
    )
)
purchase =  spark.read.csv('/FileStore/tables/train_purchases.csv', header=True)
session =  spark.read.csv('/FileStore/tables/train_sessions.csv', header=True)

In [0]:
unique_features = item_features.groupBy('item_id').agg(
    count('item_id').alias('unique_items')
).count()

print(unique_features)

23691


In [0]:
item_per_category = item_features.groupBy(
    'feature_category_id'
).agg(
    count('item_id').alias('item_per_category')
).orderBy(
    col('item_per_category').desc()
)

item_per_category.display()


feature_category_id item_per_category cat_47 23691 cat_56 23691 cat_50 23077 cat_68 23038 cat_61 22512 cat_72 20499 cat_69 20450 cat_7 20416 cat_55 17779 cat_30 15412 cat_4 14954 cat_63 14588 cat_32 14277 cat_26 14270 cat_73 13339 cat_19 12308 cat_17 12103 cat_65 10960 cat_46 10102 cat_5 9488 cat_3 9311 cat_45 9264 cat_59 8843 cat_34 7033 cat_18 6611 cat_62 6148 cat_11 6004 cat_15 5340 cat_29 4859 cat_41 4620 cat_53 3806 cat_44 3775 cat_24 3242 cat_36 2593 cat_49 2591 cat_38 2581 cat_67 2568 cat_31 2567 cat_2 2253 cat_39 2237 cat_33 2221 cat_23 2215 cat_28 1989 cat_57 1962 cat_25 1962 cat_8 1962 cat_16 1881 cat_42 1873 cat_58 1859 cat_60 1792 cat_6 1792 cat_37 1713 cat_21 1565 cat_12 1565 cat_10 1155 cat_1 941 cat_48 939 cat_66 877 cat_40 877 cat_20 846 cat_70 807 cat_14 807 cat_51 678 cat_71 671 cat_64 671 cat_22 608 cat_35 570 cat_43 569 cat_52 568 cat_54 341 cat_13 137 cat_9 137 cat_27 1

In [0]:

#to have item_id column later on
columns = ["feature_category_id"]
data = [["item_id"]]
additional_column = spark.createDataFrame(
    data=data
).toDF(
    *columns
)

#keeping most frequent items
freq_item = item_per_category.filter(
    col('item_per_category')>8000
).select(
    'feature_category_id'
    )

#heavily item per category list 
feature_indices = additional_column.unionByName(
    freq_item
).rdd.flatMap(
    lambda x: x
).collect()

freq_item.display()

feature_category_id cat_47 cat_56 cat_50 cat_68 cat_61 cat_72 cat_69 cat_7 cat_55 cat_30 cat_4 cat_63 cat_32 cat_26 cat_73 cat_19 cat_17 cat_65 cat_46 cat_5 cat_3 cat_45 cat_59

In [0]:
session = session.withColumn(
    'date_time',to_timestamp('date')
).withColumn(
    'date',to_date('date')
).dropDuplicates(
    subset = ['session_id' , 'item_id']
).withColumn(
    'dataset', lit('session')
)


session_timespent = session.groupBy(
    'session_id'
).agg(
    min('date_time').alias('min_time'),
    max('date_time').alias('max_time')
).withColumn(
    'DiffInSeconds',unix_timestamp("max_time")-unix_timestamp('min_time')
).withColumn(  
    'DiffInMinutes' , round(col('DiffInSeconds') / 60 , 2) 
)



In [0]:
session_timespent.display()

session_id min_time max_time DiffInSeconds DiffInMinutes 97872 2021-01-01T23:08:15.247+0000 2021-01-01T23:10:59.016+0000 164 2.73 123603 2021-04-13T20:46:35.506+0000 2021-04-13T20:56:28.975+0000 593 9.88 141386 2021-02-09T18:56:42.733+0000 2021-02-09T19:59:58.234+0000 3796 63.27 170392 2020-07-30T07:44:47.727+0000 2020-07-30T07:49:33.059+0000 286 4.77 183892 2021-01-11T23:09:50.300+0000 2021-01-11T23:10:39.973+0000 49 0.82 198542 2020-12-26T12:02:38.239+0000 2020-12-26T12:43:28.841+0000 2450 40.83 289064 2020-08-19T10:59:50.508+0000 2020-08-19T11:08:23.121+0000 513 8.55 292237 2020-10-30T21:25:49.896+0000 2020-10-30T21:26:01.065+0000 12 0.2 339370 2020-11-03T12:54:07.496+0000 2020-11-03T13:10:38.779+0000 991 16.52 358525 2021-04-01T19:34:49.066+0000 2021-04-01T19:44:29.016+0000 580 9.67 406733 2020-12-02T21:12:11.903+0000 2020-12-02T21:12:43.049+0000 32 0.53 553658 2021-02-27T21:06:22.437+0000 2021-02-27T21:36:11.607+0000 1789 29.82 7252 2020-09-05T06:17:43.330+0000 2020-09-05T06:40:07.442+0000 1344 22.4 37311 2020-02-06T02:52:20.553+0000 2020-02-06T14:21:44.148+0000 41364 689.4 89555 2021-03-31T20:04:17.601+0000 2021-03-31T20:57:02.905+0000 3165 52.75 101272 2020-08-26T13:34:25.991+0000 2020-08-26T13:34:25.991+0000 0 0.0 232709 2020-01-04T09:26:38.262+0000 2020-01-04T09:36:33.136+0000 595 9.92 239830 2021-05-22T12:36:36.320+0000 2021-05-22T12:40:35.498+0000 239 3.98 310550 2020-09-01T20:08:22.464+0000 2020-09-01T20:14:54.594+0000 392 6.53 321060 2020-06-29T22:23:35.681+0000 2020-06-29T22:32:47.845+0000 552 9.2 354774 2020-11-27T14:14:05.217+0000 2020-11-27T14:16:09.048+0000 124 2.07 368248 2020-06-09T05:35:39.564+0000 2020-06-09T05:41:44.474+0000 365 6.08 402516 2020-11-27T06:32:18.872+0000 2020-11-27T06:43:07.742+0000 649 10.82 467504 2020-05-30T06:34:30.635+0000 2020-05-30T07:06:23.467+0000 1913 31.88 498739 2021-05-23T12:02:04.735+0000 2021-05-23T12:11:08.421+0000 544 9.07 520942 2020-05-29T07:47:41.643+0000 2020-05-29T08:03:50.478+0000 969 16.15 541518 2021-05-13T02:16:49.330+0000 2021-05-13T02:42:12.499+0000 1523 25.38 554630 2020-07-30T15:07:49.624+0000 2020-07-30T15:10:46.433+0000 177 2.95 9030 2021-04-29T21:58:21.348+0000 2021-04-29T22:06:08.812+0000 467 7.78 97718 2021-03-04T14:53:41.685+0000 2021-03-04T19:36:02.456+0000 16941 282.35 158096 2020-12-16T13:45:20.487+0000 2020-12-16T13:48:04.511+0000 164 2.73 175080 2020-12-25T15:14:28.431+0000 2020-12-25T15:16:17.573+0000 109 1.82 206495 2020-03-20T16:03:55.526+0000 2020-03-20T16:18:50.394+0000 895 14.92 225241 2020-12-01T15:04:12.236+0000 2020-12-01T15:04:12.236+0000 0 0.0 263869 2021-01-04T19:22:19.672+0000 2021-01-04T19:36:55.800+0000 876 14.6 280271 2020-11-27T19:56:58.466+0000 2020-11-27T20:08:17.670+0000 679 11.32 404817 2021-04-15T21:49:30.731+0000 2021-04-15T21:54:29.619+0000 299 4.98 456124 2020-08-01T10:49:31.840+0000 2020-08-01T10:55:41.382+0000 370 6.17 468842 2021-03-21T14:20:24.728+0000 2021-03-21T17:17:48.700+0000 10644 177.4 478340 2020-11-27T21:22:45.344+0000 2020-11-27T21:32:22.649+0000 577 9.62 561428 2021-01-06T09:39:56.923+0000 2021-01-06T10:04:01.158+0000 1445 24.08 79757 2020-10-14T07:43:35.316+0000 2020-10-14T19:26:14.321+0000 42159 702.65 70078 2020-12-18T18:45:15.170+0000 2020-12-18T18:48:13.758+0000 178 2.97 105705 2020-06-12T12:18:27.320+0000 2020-06-12T12:18:40.146+0000 13 0.22 131450 2020-05-17T04:15:36.906+0000 2020-05-17T04:27:55.742+0000 739 12.32 146433 2020-04-18T19:58:36.978+0000 2020-04-18T20:37:03.467+0000 2307 38.45 173922 2020-08-18T12:32:27.667+0000 2020-08-18T20:09:34.080+0000 27427 457.12 176552 2020-11-27T11:51:33.794+0000 2020-11-27T11:53:47.721+0000 134 2.23 279777 2020-06-05T07:47:34.523+0000 2020-06-05T07:51:35.846+0000 241 4.02 320075 2021-04-13T20:05:09.157+0000 2021-04-13T20:05:25.565+0000 16 0.27 371660 2020-06-20T17:12:49.841+0000 2020-06-20T17:13:22.855+0000 33 0.55 406575 2021-03-01T17:41:32.518+0000 2021-03-01T17:43:19.739+0000 107 1.78 435495 2020-08-15T18:57:52.568+0000 2020-08-15T18:58:30.005+0000 38 0.63 47811

In [0]:
purchase = purchase.withColumn(
    'date_time',to_timestamp('date')
).withColumn(
    'date',to_date('date')
).dropDuplicates(
    subset = ['session_id' , 'item_id']
).withColumn(
    'dataset', lit('purchase')
)


purchase.display()


session_id item_id date date_time dataset 351 9683 2021-03-05 2021-03-05T00:00:00.000+0000 purchase 806 12516 2020-01-03 2020-01-03T00:00:00.000+0000 purchase 923 3630 2021-03-01 2021-03-01T00:00:00.000+0000 purchase 1076 13994 2020-11-30 2020-11-30T00:00:00.000+0000 purchase 1440 1812 2021-04-26 2021-04-26T00:00:00.000+0000 purchase 4252 25980 2020-07-16 2020-07-16T00:00:00.000+0000 purchase 7315 13381 2020-06-04 2020-06-04T00:00:00.000+0000 purchase 7903 13111 2020-04-12 2020-04-12T00:00:00.000+0000 purchase 8559 6511 2020-12-28 2020-12-28T00:00:00.000+0000 purchase 8938 9594 2021-05-30 2021-05-30T00:00:00.000+0000 purchase 9224 14680 2021-02-25 2021-02-25T00:00:00.000+0000 purchase 9331 11328 2020-01-13 2020-01-13T00:00:00.000+0000 purchase 9631 15998 2020-11-29 2020-11-29T00:00:00.000+0000 purchase 9713 12958 2021-05-27 2021-05-27T00:00:00.000+0000 purchase 9721 23451 2020-11-29 2020-11-29T00:00:00.000+0000 purchase 11503 16660 2020-07-02 2020-07-02T00:00:00.000+0000 purchase 11627 6848 2020-10-17 2020-10-17T00:00:00.000+0000 purchase 14089 16183 2020-08-09 2020-08-09T00:00:00.000+0000 purchase 14091 17119 2020-05-01 2020-05-01T00:00:00.000+0000 purchase 14678 27953 2021-03-31 2021-03-31T00:00:00.000+0000 purchase 15705 4193 2021-05-05 2021-05-05T00:00:00.000+0000 purchase 16263 6170 2020-01-04 2020-01-04T00:00:00.000+0000 purchase 17301 28047 2020-12-13 2020-12-13T00:00:00.000+0000 purchase 18066 9059 2020-12-02 2020-12-02T00:00:00.000+0000 purchase 18654 9905 2020-12-05 2020-12-05T00:00:00.000+0000 purchase 18903 12733 2021-03-24 2021-03-24T00:00:00.000+0000 purchase 20043 21024 2020-07-04 2020-07-04T00:00:00.000+0000 purchase 20982 7246 2021-05-31 2021-05-31T00:00:00.000+0000 purchase 22013 28063 2020-08-14 2020-08-14T00:00:00.000+0000 purchase 22245 19472 2021-05-08 2021-05-08T00:00:00.000+0000 purchase 23503 21666 2020-09-22 2020-09-22T00:00:00.000+0000 purchase 25790 18558 2020-01-25 2020-01-25T00:00:00.000+0000 purchase 26629 21193 2020-09-26 2020-09-26T00:00:00.000+0000 purchase 27614 22947 2020-08-01 2020-08-01T00:00:00.000+0000 purchase 27920 7219 2020-11-12 2020-11-12T00:00:00.000+0000 purchase 28312 18574 2020-05-23 2020-05-23T00:00:00.000+0000 purchase 28887 18847 2021-04-10 2021-04-10T00:00:00.000+0000 purchase 29103 14678 2021-05-13 2021-05-13T00:00:00.000+0000 purchase 30692 19627 2020-08-22 2020-08-22T00:00:00.000+0000 purchase 31020 2101 2020-07-10 2020-07-10T00:00:00.000+0000 purchase 37528 13207 2020-10-24 2020-10-24T00:00:00.000+0000 purchase 38357 15200 2020-02-03 2020-02-03T00:00:00.000+0000 purchase 38571 18701 2020-06-21 2020-06-21T00:00:00.000+0000 purchase 38622 8875 2020-07-06 2020-07-06T00:00:00.000+0000 purchase 38977 16544 2021-04-25 2021-04-25T00:00:00.000+0000 purchase 39723 369 2020-01-23 2020-01-23T00:00:00.000+0000 purchase 39914 14593 2020-12-18 2020-12-18T00:00:00.000+0000 purchase 40450 13698 2020-06-06 2020-06-06T00:00:00.000+0000 purchase 42123 19591 2020-07-28 2020-07-28T00:00:00.000+0000 purchase 42414 18310 2020-02-13 2020-02-13T00:00:00.000+0000 purchase 44057 9823 2020-03-16 2020-03-16T00:00:00.000+0000 purchase 44216 13632 2020-07-27 2020-07-27T00:00:00.000+0000 purchase 44417 21949 2020-10-08 2020-10-08T00:00:00.000+0000 purchase 44843 7096 2020-10-03 2020-10-03T00:00:00.000+0000 purchase 45408 23162 2020-07-26 2020-07-26T00:00:00.000+0000 purchase 45521 7219 2020-11-29 2020-11-29T00:00:00.000+0000 purchase 46280 25770 2020-01-29 2020-01-29T00:00:00.000+0000 purchase 46549 7882 2021-04-17 2021-04-17T00:00:00.000+0000 purchase 46815 3825 2021-05-23 2021-05-23T00:00:00.000+0000 purchase 46818 22751 2021-05-13 2021-05-13T00:00:00.000+0000 purchase 48719 15976 2020-06-14 2020-06-14T00:00:00.000+0000 purchase 49069 21482 2021-01-01 2021-01-01T00:00:00.000+0000 purchase 50087 5199 2021-01-06 2021-01-06T00:00:00.000+0000 purchase 50590 2393 2020-09-23 2020-09-23T00:00:00.000+0000 purchase 51292 11565 2020-07-01 2020-07-01T00:00:00.000+0000 purchase 51749 1644 2020-10-03 2020-10-03T0

In [0]:
#Create a dataframe with session and purchases for each item - to see which were in session and which was purchased 
all_session = session.unionByName(
    purchase
).orderBy(
    col('session_id').desc(),
    col('dataset').desc()
)

all_session.display()

##Create a validation Dataset

In [0]:
# #what is the latest date of the session
# last month will be validation data for out model -need to change it with last month 
val_data = all_session.filter(col('date') >= '2021-05-01')
# val_data.display()
val_data.count() 
#461813

Out[39]: 461813

##Create a train Dataset

In [0]:
# taking of the data for training our model  - for computational reasons 
train_data = all_session.filter(
    (col('date') < '2021-05-01')
)

train_data.count() #4647037

Out[15]: 4647037

##Create  df with items containing the most frequent feature categories

In [0]:
from pyspark.sql.types import *
#creating a pivot table that has the item id as rows  and the categories as columns  of the most frequent items and shows the category_value id
item_features_pivot = item_features.withColumn(
    'feature_value_id',col('feature_value_id').cast(IntegerType())
).groupBy(
    "item_id"
).pivot(
    "feature_category_id"
).sum(
    'feature_value_id'
)

items_dataset = item_features_pivot.select(
    feature_indices #most frequent categories
)

# this will show a df with the it_id | session_id | date| either session or purchase of the the items along with the categories(of the most frequent categories)

train_data_with_features = train_data.join(
    items_dataset,
    on='item_id',
    how='left'
).orderBy(
    col('session_id').desc(),
    col('dataset').desc()
)

train_data_with_features.display()

item_id session_id date date_time dataset cat_47 cat_56 cat_50 cat_68 cat_61 cat_72 cat_69 cat_7 cat_55 cat_30 cat_4 cat_63 cat_32 cat_26 cat_73 cat_19 cat_17 cat_65 cat_46 cat_5 cat_3 cat_45 cat_59 4892 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 603 365 240 351 462 75 885 837 267 null 618 861 902 268 544 288 378 null 825 605 793 559 856 17564 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 240 596 462 75 709 837 267 null 618 861 902 268 544 765 378 null 825 605 793 559 856 1687 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 901 745 706 75 709 837 267 null 618 861 902 268 544 112 378 null 825 605 793 559 180 3122 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 240 875 706 455 709 837 267 null 618 861 902 346 544 765 378 null 825 605 793 559 180 23611 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 240 373 706 455 709 837 267 null 618 861 902 268 544 765 378 null 825 605 793 559 180 291 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 240 373 706 371 709 837 129 669 618 861 902 268 544 765 378 null 825 605 793 559 180 14190 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 240 379 462 75 709 837 267 null 618 861 902 268 544 292 378 null 825 605 793 559 180 16962 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 690 365 240 351 462 75 709 837 267 null 618 861 902 77 544 765 378 null 825 605 793 559 856 12263 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 603 365 240 373 462 75 885 837 267 null 618 861 902 268 544 288 378 null 825 605 793 559 856 17058 999998 2020-11-27 2020-11-27T00:00:00.000+0000 session 549 365 240 351 706 75 709 837 267 null 618 861 902 268 544 765 378 521 825 605 793 559 180 23597 999998 2020-11-27 2020-11-27T14:55:19.785+0000 purchase 690 365 240 596 462 75 709 837 267 null 618 861 902 268 544 292 378 null 825 605 793 559 387 1206 999997 2021-02-18 2021-02-18T00:00:00.000+0000 session 123 365 317 739 462 75 885 394 267 null 618 861 null null 544 null null null null null null null null 19715 999997 2021-02-18 2021-02-18T11:56:34.432+0000 purchase 123 365 317 739 462 75 885 394 267 null 618 861 null null 544 null null null null null null null null 19639 999995 2020-05-11 2020-05-11T00:00:00.000+0000 session 36 408 708 31 898 75 780 2 null null null null 522 507 null 628 null null 882 58 null null null 25007 999995 2020-05-11 2020-05-11T16:13:27.403+0000 purchase 36 408 708 31 898 75 780 2 267 null 618 861 522 507 544 112 378 521 825 396 793 559 null 11060 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 36 365 901 351 706 655 592 2 823 1041 618 861 522 507 544 700 378 521 825 605 793 559 null 6588 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 516 365 240 351 898 75 694 284 267 null 618 861 null null 544 null 378 521 null null null null null 18485 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 36 365 240 351 706 7 592 452 167 null 618 861 902 268 544 765 378 521 825 605 793 559 null 7525 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 549 365 240 373 898 75 592 2 267 null 618 861 902 268 544 254 378 521 825 605 793 559 856 15314 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 36 408 240 659 898 263 592 2 390 null 505 202 522 44 544 700 378 521 825 605 793 559 null 745 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 549 365 240 373 462 75 780 2 267 null 618 861 902 268 544 700 378 521 825 605 793 559 180 10117 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 516 365 240 445 462 75 592 619 267 null 618 861 null null 544 null 378 521 null null null null null 13620 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 842 365 240 373 706 381 592 221 43 null 385 595 902 268 544 null 378 null 825 605 793 559 null 26811 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 36 365 240 351 898 263 592 452 632 null 618 861 286 126 544 700 378 521 825 58 793 559 null 18764 999990 2020-12-16 2020-12-16T00:00:00.000+0000 session 36 365 240 351 898 75 592 490 26

## Preprocessing of the Training Set

In [0]:

#computing the average of the feature value for each category for each session 
average_category_persession = train_data_with_features.groupBy(
    'session_id'
).agg(
    avg('cat_47').alias("avg_cat_47"),                       
    avg('cat_56').alias("avg_cat_56"),
    avg('cat_50').alias("avg_cat_50"),        
    avg('cat_68').alias("avg_cat_68"),
    avg('cat_61').alias("avg_cat_61"),
    avg('cat_72').alias("avg_cat_72"),
    avg('cat_69').alias("avg_cat_69"),
    avg('cat_7').alias("avg_cat_7"),
    avg('cat_55').alias("avg_cat_55"),
    avg('cat_30').alias("avg_cat_30"),
    avg('cat_4').alias("avg_cat_4"),
    avg('cat_63').alias("avg_cat_63"),
    avg('cat_32').alias("avg_cat_32"),
    avg('cat_26').alias("avg_cat_26"),
    avg('cat_73').alias("avg_cat_73"),
    avg('cat_19').alias("avg_cat_19"),
    avg('cat_17').alias("avg_cat_17"),
    avg('cat_65').alias("avg_cat_65"),
    avg('cat_46').alias("avg_cat_46"),
    avg('cat_5').alias("avg_cat_5"),
    avg('cat_3').alias("avg_cat_3"),
    avg('cat_45').alias("avg_cat_45"),
    avg('cat_59').alias("avg_cat_59")
  
)

#create the column, with avg Feautures
avg_item=freq_item.withColumn('feature_category_id',concat(lit('avg_'),'feature_category_id'))

#join pivot table with avg table
merged_df = train_data_with_features.join(
    average_category_persession,
    on='session_id',
    how='left'
)

#Replace null in pivot with avg value of the session of the feature
for i in range(freq_item.count()):
    merged_df= merged_df.withColumn(
    freq_item.collect()[i][0] , when(
        col(freq_item.collect()[i][0]).isNull() , col(avg_item.collect()[i][0])
    ).otherwise(
        col(freq_item.collect()[i][0])
    )
)
    
#keep initial pivot columns with updated values of null's    --each null will be replaced with the avg value of the feature of each session
sessions_features_means = merged_df.select(
    train_data_with_features.columns
)

#Normalize category feature values  by dividing the max value in each column (cat_*) --TAKES 20 MINUTES!
for i in range(freq_item.count()):
    
   sessions_features_means = sessions_features_means.withColumn(
   freq_item.collect()[i][0], (col(freq_item.collect()[i][0]) / sessions_features_means.select(max(freq_item.collect()[i][0])).collect()[0][0])   
)

sessions_features_means.write.option(
  "path", "/FileStore/tables/train_sessions_normalized_all/"
).saveAsTable(
    "train_sessions_normalized_final"
 )

sessions_features_means.display()

item_id session_id date date_time dataset cat_47 cat_56 cat_50 cat_68 cat_61 cat_72 cat_69 cat_7 cat_55 cat_30 cat_4 cat_63 cat_32 cat_26 cat_73 cat_19 cat_17 cat_65 cat_46 cat_5 cat_3 cat_45 cat_59 16464 1062374 2020-08-10 2020-08-10T00:00:00.000+0000 session 0.24660633484162897 0.03686635944700461 1.0 0.4130675526024363 0.7861915367483296 0.43148357870894677 0.5638418079096045 0.9522673031026253 0.9726962457337884 0.3736842105263158 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 null 0.19121447028423771 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.7261538461538461 0.8920134983127109 0.6218020022246941 0.2102803738317757 10013 1062374 2020-08-10 2020-08-10T14:16:31.870+0000 purchase 0.18665158371040724 0.4205069124423963 1.0 0.11738648947951273 0.8997772828507795 0.08493771234428087 0.8813559322033898 0.002386634844868735 0.3037542662116041 0.3736842105263158 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 null 0.19121447028423771 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.7261538461538461 0.8920134983127109 0.6218020022246941 0.2102803738317757 5932 1062416 2020-12-16 2020-12-16T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 0.2663706992230855 0.8183831672203765 0.7861915367483296 0.08493771234428087 0.9096045197740112 0.4701670644391408 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 551 1062416 2020-12-16 2020-12-16T11:29:33.876+0000 purchase 0.13914027149321267 0.4205069124423963 0.2663706992230855 0.8183831672203765 0.5144766146993318 0.08493771234428087 0.9096045197740112 0.4701670644391408 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 13586 1062439 2020-08-05 2020-08-05T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 0.7857935627081021 0.8183831672203765 0.5144766146993318 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.3736842105263158 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 17979 1062439 2020-08-05 2020-08-05T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 0.2663706992230855 0.11738648947951273 0.5144766146993318 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.43628389154704944 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 3402 1062439 2020-08-05 2020-08-05T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 0.7857935627081021 0.8183831672203765 0.5144766146993318 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.43628389154704944 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 22607 1062439 2020-08-05 2020-08-05T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 0.8179800221975583 0.38870431893687707 0.7861915367483296 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.43628389154704944 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 7984 1062439 2020-08-05 2020-08-05T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 1.0 0.38870431893687707 0.5144766146993318 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.43628389154704944 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 3432 1062439 2020-08-05 2020-08-05T00:00:00.000+0000 session 0.13914027149321267 0.4205069124423963 0.7857935627081021 0.8183831672203765 0.7861915367483296 0.08493771234428087 0.9096045197740112 0.4701670644391408 0.3037542662116041 0.6497607655502392 0.23732718894009217 0.9706877113866967 null null 1.0 null null null null null null null null 12521 1062439 2020-08-05 2020-08-05T02:03:43.237+0000 purchase 0.13914027149321267 0.4205069124423963 1.0 0.11738648947951273 0.7861915367483296 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.2854066

## Preprocessing of the Validation set

In [0]:
# Join val_data and  the items dataset(the categories of the most frequent items) 
val_data_with_features = val_data.join(
    items_dataset,
    on='item_id',
    how='left'
).orderBy(
    col('session_id').desc(),
    col('dataset').desc()
)

import pyspark.sql.functions as f
#computing the average of the feature value for each category for each session 
val_average_category_persession = val_data_with_features.groupBy(
    'session_id'
).agg(
#     [avg(f.col(freq_item.collect()[i][0]))for i in range(freq_item.count())]
    avg('cat_47').alias("avg_cat_47"),                       
    avg('cat_56').alias("avg_cat_56"),
    avg('cat_50').alias("avg_cat_50"),        
    avg('cat_68').alias("avg_cat_68"),
    avg('cat_61').alias("avg_cat_61"),
    avg('cat_72').alias("avg_cat_72"),
    avg('cat_69').alias("avg_cat_69"),
    avg('cat_7').alias("avg_cat_7"),
    avg('cat_55').alias("avg_cat_55"),
    avg('cat_30').alias("avg_cat_30"),
    avg('cat_4').alias("avg_cat_4"),
    avg('cat_63').alias("avg_cat_63"),
    avg('cat_32').alias("avg_cat_32"),
    avg('cat_26').alias("avg_cat_26"),
    avg('cat_73').alias("avg_cat_73"),
    avg('cat_19').alias("avg_cat_19"),
    avg('cat_17').alias("avg_cat_17"),
    avg('cat_65').alias("avg_cat_65"),
    avg('cat_46').alias("avg_cat_46"),
    avg('cat_5').alias("avg_cat_5"),
    avg('cat_3').alias("avg_cat_3"),
    avg('cat_45').alias("avg_cat_45"),
    avg('cat_59').alias("avg_cat_59")
  
)


#create the column, with avg Feautures
#avg_item=freq_item.withColumn('feature_category_id',concat(lit('avg_'),'feature_category_id'))

#join pivot table with avg values  table
val_merged_df = val_data_with_features.join(
    val_average_category_persession, #df with the items with the most frequent categories 
    on='session_id',
    how='left'
)


#Replace null in pivot with avg value of the session of the feature
for i in range(freq_item.count()):
    val_merged_df= val_merged_df.withColumn(
    freq_item.collect()[i][0] , when(
        col(freq_item.collect()[i][0]).isNull() , col(avg_item.collect()[i][0])
    ).otherwise(
        col(freq_item.collect()[i][0])
    )
)
    
#keep initial pivot columns with updated values of null's    --each null will be replaced with the avg value of the feature of each session
val_sessions_features_means =val_merged_df.select(
    val_data_with_features.columns
)


#Normalize category feature values  by dividing the max value in each column (cat_*) --TAKES 26 MINUTES!
for i in range(freq_item.count()):
    
   val_sessions_features_means = val_sessions_features_means.withColumn(
   freq_item.collect()[i][0], (col(freq_item.collect()[i][0]) / val_sessions_features_means.select(max(freq_item.collect()[i][0])).collect()[0][0])   
)
val_sessions_features_means.write.option(
"path", "/FileStore/tables/validation_sessions_normalized_all"
).saveAsTable("validation_sessions_normalized_all")  

##Loading the Tables and Feed to ALS Model

In [0]:
train_table = spark.read.format('delta').load('/FileStore/tables/train_sessions_normalized_all')
val_table = spark.read.format('delta').load('/FileStore/tables/validation_sessions_normalized_all')
#has both sessions items and purchased items 

In [0]:
# join train_table with purchases  --enroll the purchased into the session dataset
sessions_features_with_purchased_items = train_table.join(
    purchase.drop(
        "date"
    ).withColumnRenamed("item_id","purchsed_item"),
    on="session_id",
    how='left'
)

cols_to_drop= ["date" ,"date_time", "purchsed_item", "dataset"]  # i have integrated the purchased into the session

train_data = sessions_features_with_purchased_items.drop(*cols_to_drop)

training_data = train_data.withColumnRenamed(
    'cat_47','x_cat_47'
).withColumnRenamed(
    'cat_56','x_cat_56'
).withColumnRenamed(
    'cat_50','x_cat_50'
).withColumnRenamed(
    'cat_68','x_cat_68'
).withColumnRenamed(
    'cat_61','x_cat_61'
).withColumnRenamed(
    'cat_72','x_cat_72'
).withColumnRenamed(
    'cat_69','x_cat_69'
).withColumnRenamed(
    'cat_7','x_cat_7'
).withColumnRenamed(
    'cat_55','x_cat_55'
).withColumnRenamed(
    'cat_30','x_cat_30'
).withColumnRenamed(
    'cat_4','x_cat_4'
).withColumnRenamed(
    'cat_63','x_cat_63'
).withColumnRenamed(
    'cat_32','x_cat_32'
).withColumnRenamed(
    'cat_26','x_cat_26'
).withColumnRenamed(
    'cat_73','x_cat_73'
).withColumnRenamed(
    'cat_19','x_cat_19'
).withColumnRenamed(
    'cat_17','x_cat_17'
).withColumnRenamed(
    'cat_65','x_cat_65'
).withColumnRenamed(
    'cat_46','x_cat_46'
).withColumnRenamed(
    'cat_5','x_cat_5'
).withColumnRenamed(
    'cat_3','x_cat_3'
).withColumnRenamed(
    'cat_45','x_cat_45'
).withColumnRenamed(
    'cat_59','x_cat_59'
).drop(*cols_to_drop)                                    

training_data.display()

session_id item_id x_cat_47 x_cat_56 x_cat_50 x_cat_68 x_cat_61 x_cat_72 x_cat_69 x_cat_7 x_cat_55 x_cat_30 x_cat_4 x_cat_63 x_cat_32 x_cat_26 x_cat_73 x_cat_19 x_cat_17 x_cat_65 x_cat_46 x_cat_5 x_cat_3 x_cat_45 x_cat_59 100010 23726 0.04072398190045249 0.4205069124423963 0.2663706992230855 0.38870431893687707 0.7861915367483296 0.6308040770101925 0.6689265536723163 0.5393794749403341 0.800910125142207 null 0.2853302611367127 0.9199549041713642 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.19688542825361513 null 100010 24874 0.9524886877828054 0.4205069124423963 1.0 0.38870431893687707 0.5144766146993318 0.08493771234428087 0.6689265536723163 0.49403341288782815 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 null 1000795 23065 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.7774086378737541 0.5144766146993318 0.8471121177802945 0.8011299435028248 0.9988066825775657 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 1.0 0.4441591784338896 1.0 0.9883720930232558 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.2102803738317757 1000795 23241 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.4130675526024363 0.7861915367483296 0.08493771234428087 0.8011299435028248 0.9988066825775657 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.2102803738317757 1000795 10782 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.22591362126245848 0.7861915367483296 0.8471121177802945 0.8011299435028248 0.9988066825775657 0.9362912400455062 null 0.23732718894009217 0.9706877113866967 1.0 0.4441591784338896 1.0 0.9883720930232558 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.45210280373831774 1000795 25855 0.7805429864253394 0.27534562211981567 0.2663706992230855 0.42414174972314506 0.7861915367483296 0.5152887882219706 0.8011299435028248 0.9988066825775657 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.45210280373831774 1000795 24625 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.4130675526024363 0.5144766146993318 0.08493771234428087 0.8011299435028248 0.9988066825775657 0.9362912400455062 null 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.45210280373831774 1000795 11098 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.9689922480620154 0.7861915367483296 0.5152887882219706 0.8011299435028248 0.9988066825775657 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.14470284237726097 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.2102803738317757 1000795 26412 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.9689922480620154 0.7861915367483296 0.5152887882219706 0.8011299435028248 0.9988066825775657 0.3037542662116041 null 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 null 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.2102803738317757 100227 17376 0.13914027149321267 0.4205069124423963 0.36403995560488345 0.8239202657807309 0.5144766146993318 0.08493771234428087 1.0 0.4701670644391408 0.3037542662116041 0.24904306220095693 0.23732718894009217 0.970687711386696

In [0]:
training_sum_vecs = training_data.na.fill(0).withColumn(
    "sum",
    ( col('x_cat_47')+
      col('x_cat_56')+
      col('x_cat_50')+
      col('x_cat_68')+
      col('x_cat_61')+
      col('x_cat_72')+
      col('x_cat_69')+
      col('x_cat_7')+
      col('x_cat_55')+
      col('x_cat_30')+
      col('x_cat_4')+
      col('x_cat_63')+
      col('x_cat_32')+
      col('x_cat_26')+
      col('x_cat_73')+
      col('x_cat_19')+
      col('x_cat_17')+
      col('x_cat_65')+
      col('x_cat_46')+
      col('x_cat_5')+
      col('x_cat_3')+
      col('x_cat_45')+
      col('x_cat_59')
    )
)
training_sum_vecs.display()
# df1.show()


session_id item_id x_cat_47 x_cat_56 x_cat_50 x_cat_68 x_cat_61 x_cat_72 x_cat_69 x_cat_7 x_cat_55 x_cat_30 x_cat_4 x_cat_63 x_cat_32 x_cat_26 x_cat_73 x_cat_19 x_cat_17 x_cat_65 x_cat_46 x_cat_5 x_cat_3 x_cat_45 x_cat_59 sum 1000415 20536 0.04072398190045249 0.4205069124423963 0.3518312985571587 0.8250276854928018 0.5144766146993318 0.08493771234428087 0.9096045197740112 0.639618138424821 0.3037542662116041 0.4110047846889952 0.23732718894009217 0.9706877113866967 0.5787139689578714 0.05648267008985879 1.0 0.14470284237726097 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 1.0 13.056143918364334 1000415 22146 0.583710407239819 0.4205069124423963 0.3518312985571587 0.991140642303433 0.7861915367483296 0.08493771234428087 1.0 0.7386634844868735 0.3037542662116041 0.4110047846889952 0.23732718894009217 0.9706877113866967 0.7893569844789357 0.10077021822849808 1.0 0.14470284237726097 0.6156351791530945 0.7503075030750308 0.8656873032528857 0.9307692307692308 0.8087739032620922 0.6218020022246941 1.0 14.507561112171405 1000415 17503 0.6210407239819005 0.4205069124423963 0.3518312985571587 0.4130675526024363 0.7861915367483296 0.08493771234428087 0.9096045197740112 0.639618138424821 0.3037542662116041 0.4110047846889952 0.23732718894009217 0.9706877113866967 1.0 0.14505776636713735 1.0 0.14470284237726097 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.9307692307692308 0.7255343082114736 0.6218020022246941 1.0 13.839597386822586 1000615 18068 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.9689922480620154 0.5144766146993318 0.08493771234428087 0.8011299435028248 0.9988066825775657 0.3037542662116041 0.0 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 0.6721138639957829 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 1.0 15.277956945276028 1000615 24896 0.583710407239819 0.4205069124423963 0.2663706992230855 0.8250276854928018 0.5484409799554566 0.08493771234428087 0.607909604519774 0.9522673031026253 0.3037542662116041 0.0 0.2446236559139785 0.9706877113866967 0.9297856614929785 0.2894736842105263 1.0 0.5734280792420327 0.6156351791530945 0.7503075030750308 0.8656873032528857 0.8966666666666667 0.8920134983127109 0.6218020022246941 0.7367601246105918 13.979796640073731 1000615 25893 0.24660633484162897 0.4205069124423963 0.2663706992230855 0.530454042081949 0.5144766146993318 0.08493771234428087 0.5638418079096045 0.9522673031026253 0.3037542662116041 0.0 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.9883720930232558 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 1.0 13.990377117012391 1000615 11937 0.6210407239819005 0.4205069124423963 0.2663706992230855 0.530454042081949 0.5484409799554566 0.08493771234428087 0.5638418079096045 0.639618138424821 0.3037542662116041 0.0 0.23732718894009217 0.9706877113866967 0.5787139689578714 0.01668806161745828 1.0 0.7041343669250646 0.6156351791530945 0.6408364083640836 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 1.0 13.053260202478981 1000615 15651 0.7805429864253394 0.4205069124423963 0.2663706992230855 0.4130675526024363 0.5144766146993318 0.08493771234428087 0.8011299435028248 0.9988066825775657 0.3037542662116041 0.0 0.23732718894009217 0.9706877113866967 1.0 0.34403080872913994 1.0 0.3772609819121447 0.6156351791530945 0.6721138639957829 0.8656873032528857 0.9307692307692308 0.8920134983127109 0.6218020022246941 0.2102803738317757 13.321201512537112 1000615 8807 0.583710407239819 0.4205069124423963 0.2663706992230855 0.6600221483942414 0.5144766146993318 0.08493771234428087 0.607909604519774 0.9522673031026253 0.3037542662116041 0.0 0.2446236559139785 0.9706877113866967 0.9297856614929785 0.2894736842105263 1.0 0.5734280792420327 0.6156351791530945 0.7503075030750308 0.8656873032528857 0.89666666666

In [0]:
#Unseen Data Set 
val_sessions_features_with_purchased_items = val_table.join(
    purchase.drop(
        "date").withColumnRenamed("item_id","purchsed_item"),
    on="session_id",
    how='left'
)

# cols_to_drop= ["date" ,"date_time" , "dataset",'cat_47','cat_56','cat_50','cat_68','cat_61','cat_72','cat_69' ,'cat_7','cat_55','cat_30','cat_4','cat_63','cat_32',
#                'cat_26','cat_73','cat_19','cat_17','cat_65','cat_46','cat_5','cat_3','cat_45','cat_59']
cols_to_drop= ["date" ,"date_time" , "dataset"]

test_data = val_sessions_features_with_purchased_items.withColumn(
    "session_id", col("session_id").cast(DoubleType())
).withColumn(
    "item_id", col("item_id").cast(DoubleType())
).withColumn(
    "purchsed_item", col("purchsed_item").cast(DoubleType())
).drop(*cols_to_drop)

test_data.display()

In [0]:
#FineTune the Model Using ParamGridBuilder
from pyspark.ml.tuning import  TrainValidationSplit , ParamGridBuilder
from pyspark.ml.recommendation import ALS 
from pyspark.ml.evaluation import RegressionEvaluator


#  split the training data into train and val(test)
training ,test  =training_sum_vecs.withColumn(
    "session_id", col("session_id").cast(DoubleType())
).withColumn(
    "item_id", col("item_id").cast(DoubleType())
).randomSplit([0.7, 0.3]) # training the model

als = ALS(
    implicitPrefs=True, 
    userCol="session_id", 
    itemCol= "item_id",
    ratingCol = "sum" , 
    coldStartStrategy="drop",
    nonnegative=True
)

param_grid = ParamGridBuilder().addGrid(als.rank , [15,20]).addGrid(als.maxIter , [5, 10]).addGrid(als.regParam , [0.02, 0.10]).build() 
evaluator2 = RegressionEvaluator(metricName="rmse",labelCol="sum",predictionCol="prediction")

#Build cross validation using TrainValidationSplit 
tvs = TrainValidationSplit(estimator=als , estimatorParamMaps =  param_grid , evaluator = evaluator2)

#fit ALS  to the training data 
model2 =tvs.fit(training)

#extract best model from the tuning excerice using ParamGridBuilder 
best_model= model2.bestModel

#Generate Predictins and evaluate the RMSE 

predictions2 = best_model.transform(test)
rmse2 = evaluator2.evaluate(predictions2)

print("RMSE = " + str(rmse2))
print("*** BEST MODEL ***")
print(" Rank: ", best_model.rank)
print(" MaxIter: ", best_model._java_obj.parent().getMaxIter())
print(" RegParam: ", best_model._java_obj.parent().getRegParam())


# RMSE = 12.215137151013003
# *** BEST MODEL ***
#  Rank:  15
#  MaxIter:  11
#  RegParam:  0.15


# RMSE = 12.232727214428332
# *** BEST MODEL ***
#  Rank:  8
#  MaxIter:  10
#  RegParam:  0.1

# RMSE = 12.21054187852252
# *** BEST MODEL ***
#  Rank:  20
#  MaxIter:  10
#  RegParam:  0.1

RMSE = 12.21054187852252
*** BEST MODEL ***
 Rank:  20
 MaxIter:  10
 RegParam:  0.1


In [0]:
# Save & load the model
rfPath = "/FileStore/tables/ALSFinal"
best_model.save(rfPath)
samealsModel = ALS.load(rfPath)


# Save and load model
model.save(sc, "target/tmp/myCollaborativeFilter")
sameModel = MatrixFactorizationModel.load(sc, "target/tmp/myCollaborativeFilter")
dbutils.fs.rm("/FileStore/tables/train_sessions_normalized_fina;.csv")


---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
<command-3694853921792726> in <module>
      2 rfPath = "/FileStore/tables/ALSFinal"
      3 best_model.save(rfPath)
----> 4 samealsModel = ALS.load(rfPath)

/databricks/spark/python/pyspark/ml/util.py in load(cls, path)
    461     def load(cls, path):
    462         """Reads an ML instance from the input path, a shortcut of `read().load(path)`."""
--> 463         return cls.read().load(path)
    464 
    465 

/databricks/spark/python/pyspark/ml/util.py in load(self, path)
    411         if not isinstance(path, str):
    412             raise TypeError("path should be a string, got type %s" % type(path))
--> 413         java_obj = self._jread.load(path)
    414         if not hasattr(self._clazz, "_from_java"):
    415             raise NotImplementedError("This Java ML type cannot be loaded into Python currently: %r"

/databricks/s

In [0]:
results = best_model.recommendForAllUsers(5).withColumn(
    'next_item', explode('recommendations')
).withColumn(
    'item', col('next_item').item_id
).withColumn(
    'ranking', col('next_item').rating
).select('session_id','item','ranking')
# # get the name and the name in separate columns
# df=df.withColumn('name', F.col('exploded').getItem(0))
# df=df.withColumn('value', F.col('exploded').getItem(1))
results.display()

session_id item ranking 28 10390 0.44238698 28 18705 0.32970768 28 14550 0.3241707 28 412 0.32254535 28 25809 0.2926991 31 19882 0.29711872 31 2915 0.19427127 31 24874 0.19111024 31 18719 0.19042684 31 2188 0.1825643 44 4028 0.56548727 44 9184 0.55949545 44 23088 0.47771543 44 1018 0.4624759 44 17089 0.45589846 108 16658 0.49863452 108 19170 0.44174343 108 27455 0.39297232 108 6372 0.39078087 108 11386 0.38783708 384 27856 0.019818507 384 24269 0.018178817 384 4528 0.017048799 384 5858 0.016431598 384 23138 0.0154363895 412 24269 0.20705841 412 4528 0.18965983 412 5858 0.18793559 412 2447 0.18531755 412 23138 0.17582192 496 8060 0.70449334 496 18156 0.47583508 496 20770 0.41157523 496 24921 0.37486854 496 15501 0.3595335 540 13540 0.44882697 540 6146 0.39143816 540 27416 0.36322132 540 1272 0.35447833 540 10717 0.35233745 606 24243 0.07712601 606 19170 0.06641324 606 16658 0.06349236 606 16064 0.051976353 606 24545 0.05158122 633 8861 0.18510617 633 22886 0.14305568 633 18415 0.10758997 633 20574 0.10550687 633 18623 0.103227444 642 13409 0.2932751 642 19227 0.2851599 642 3591 0.25632322 642 4635 0.2473832 642 21906 0.23266548 688 19227 0.26026928 688 13409 0.24100266 688 3591 0.22819203 688 4635 0.22579001 688 14330 0.20361 756 10390 0.049117256 756 18705 0.03660672 756 14550 0.03599196 756 412 0.035811502 756 18175 0.033466615 799 10390 0.39302725 799 18705 0.29292026 799 14550 0.28800103 799 412 0.28655705 799 25809 0.26004094 806 19170 0.14617057 806 16658 0.13011472 806 24243 0.123793095 806 8861 0.11952294 806 23088 0.11078504 808 26853 0.69926625 808 17089 0.6743125 808 24930 0.5207716 808 6736 0.46588156 808 639 0.45261002 811 8622 1.0066054 811 972 0.62756556 811 12251 0.62677574 811 23450 0.5712934 811 11491 0.5489134 842 26853 0.35866767 842 4193 0.2525315 842 6736 0.22734196 842 21616 0.21688949 842 26249 0.18009803 844 19227 0.09343835 844 13409 0.086521514 844 3591 0.08192241 844 4635 0.08106007 844 27852 0.07959492 857 8060 0.15077823 857 8622 0.13086987 857 18156 0.10183995 857 20770 0.09808721 857 21781 0.08715007 916 4028 0.512827 916 9184 0.5075676 916 23088 0.43337768 916 1018 0.41955256 916 13922 0.37039044 1031 19882 0.25079706 1031 2915 0.1639838 1031 24874 0.1613156 1031 18719 0.16073875 1031 2188 0.154102 1143 19882 0.83779675 1143 2915 0.5477939 1143 24874 0.5388807 1143 18719 0.5369537 1143 2188 0.5147834 1199 2447 0.5087425 1199 2855 0.3336055 1199 27555 0.32978863 1199 17780 0.24756125 1199 8060 0.24384743 1259 26301 0.24784692 1259 2072 0.23796134 1259 26691 0.2319535 1259 5704 0.21286602 1259 7872 0.19986421 1274 19170 0.08244699 1274 16658 0.081874296 1274 24243 0.06982506 1274 24545 0.065475844 1274 23088 0.062487908 1303 2447 0.030056428 1303 2855 0.024624432 1303 27555 0.024342695 1303 8861 0.02397632 1303 8616 0.019366547 1417 26301 0.35590535 1417 2072 0.34933075 1417 26691 0.33076826 1417 5704 0.3044909 1417 7872 0.28892604 1441 2072 0.12976061 1441 26301 0.12649709 1441 26691 0.11744016 1441 5704 0.10777599 1441 7872 0.10209641 1500 19227 0.0014442863 1500 13409 0.001337372 1500 3591 0.0012662832 1500 4635 0.0012529539 1500 14330 0.0011298726 1537 13409 0.36768115 1537 24243 0.33920544 1537 19596 0.3141874 1537 26897 0.30454177 1537 19227 0.2580875 1721 12179 0.16329817 1721 6372 0.14508924 1721 3985 0.14188759 1721 19945 0.14023757 1721 3257 0.13693038 1816 26853 0.578686 1816 19882 0.46816087 1816 6736 0.366656 1816 4193 0.3659929 1816 15738 0.36344096 1829 7963 0.42633498 1829 4028 0.39838207 1829 9184 0.39422506 1829 23088 0.33660218 1829 1018 0.3258643 1863 13540 0.27379906 1863 6146 0.23879002 1863 27416 0.22157682 1863 1272 0.21624331 1863 10717 0.21493731 1869 6372 0.25514337 1869 3985 0.24912632 1869 19945 0.24652235 1869 12179 0.21797818 1869 15114 0.20949951 1884 27852 0.18434471 1884 23789 0.16899288 1884 13897 0.13546726 1884 16749 0.13502406 1884 4193 0.12999429 1889 2072 0.19466105 1889 2447 0.17713363 1889 27555 0.15625708 1889 26301 0.14745408 1889 2855 0.14512087 1892 27